In [117]:
from datetime import timedelta
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
from itertools import chain, combinations, permutations
import numpy as np

In [118]:
df = pd.read_parquet('../../Sonar/seatunnel_all_information.parquet')

In [119]:
df['time'] = df['total_time'].astype('int64')

In [120]:
X = df.loc[:, ~df.columns.isin(['begin_sha', 'end_sha', 'begin_time', 'end_time',
                                'total_time',
                                # 'time'
                                ])]

In [121]:
X.head(1)

commits  additions  deletions  changed_files begin_Dispensables  \
0        1         10          4              3              500.0   

   begin_Bloaters  begin_Change Preventers  begin_Couplers  \
0           262.0                    262.0           304.0   

   begin_Object-Orientation Abusers  end_Dispensables  end_Bloaters  \
0                             304.0             500.0         261.0   

   end_Change Preventers  end_Couplers  end_Object-Orientation Abusers  \
0                  261.0         304.0                           693.0   

              time  
0  264468000000000

In [122]:
# Step 1: Loop through combinations
def column_combinations(data_frame):
    columns = data_frame.columns
    col_combinations = []

    for r in range(1, len(columns) + 1):
        for combo in combinations(columns, r):
            col_combinations.append(combo)

    return col_combinations

# Example usage:
data = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6], 'C': [7, 8, 9]})
combinations = column_combinations(X)
print(combinations)


[('commits',), ('additions',), ('deletions',), ('changed_files',), ('begin_Dispensables',), ('begin_Bloaters',), ('begin_Change Preventers',), ('begin_Couplers',), ('begin_Object-Orientation Abusers',), ('end_Dispensables',), ('end_Bloaters',), ('end_Change Preventers',), ('end_Couplers',), ('end_Object-Orientation Abusers',), ('time',), ('commits', 'additions'), ('commits', 'deletions'), ('commits', 'changed_files'), ('commits', 'begin_Dispensables'), ('commits', 'begin_Bloaters'), ('commits', 'begin_Change Preventers'), ('commits', 'begin_Couplers'), ('commits', 'begin_Object-Orientation Abusers'), ('commits', 'end_Dispensables'), ('commits', 'end_Bloaters'), ('commits', 'end_Change Preventers'), ('commits', 'end_Couplers'), ('commits', 'end_Object-Orientation Abusers'), ('commits', 'time'), ('additions', 'deletions'), ('additions', 'changed_files'), ('additions', 'begin_Dispensables'), ('additions', 'begin_Bloaters'), ('additions', 'begin_Change Preventers'), ('additions', 'begin_Co

In [123]:
# # Step 2: Prepare the data set from loop combinations
# def prepare_data_set(data_frame, combination):
#     subset = data_frame[list(combination)]
#     return subset

In [124]:
# Step 3: Use MinMaxScaler
def scale_data(data,columns):
    scaler = MinMaxScaler()
    scaled_data = scaler.fit_transform(data[columns])

    return pd.DataFrame(scaled_data)

In [125]:
co = scale_data(X, X.columns)
co

0         1         2         3         4         5         6   \
0     0.000000  0.000262  0.000143  0.001679  0.992032  0.918440  0.918440   
1     0.000000  0.000052  0.000036  0.000560  0.992032  0.918440  0.918440   
2     0.000000  0.000944  0.002393  0.005036  0.992032  0.918440  0.918440   
3     0.000000  0.000551  0.000071  0.001679  0.992032  0.918440  0.918440   
4     0.060870  0.005536  0.007571  0.044768  0.990040  0.914894  0.914894   
...        ...       ...       ...       ...       ...       ...       ...   
1063  0.026087  0.005011  0.001428  0.006715  0.027888  0.039007  0.039007   
1064  0.043478  0.012330  0.001500  0.008954  0.023904  0.031915  0.031915   
1065  0.008696  0.001810  0.001750  0.005036  0.023904  0.031915  0.031915   
1066  0.000000  0.000289  0.040283  0.015109  0.000000  0.000000  0.000000   
1067  0.000000  0.000944  0.000000  0.000560  0.000000  0.000000  0.000000   

            7         8         9         10        11        12        13  \
0     0.990132  0.990132  0.991837  0.912088  0.912088  0.990000  0.995208   
1     0.990132  0.990132  0.993878  0.915751  0.915751  0.990000  0.995208   
2     0.990132  0.990132  0.989796  0.912088  0.912088  0.990000  0.995208   
3     0.990132  0.990132  0.991837  0.912088  0.912088  0.990000  0.995208   
4     0.990132  0.990132  0.991837  0.915751  0.915751  0.990000  0.995208   
...        ...       ...       ...       ...       ...       ...       ...   
1063  0.013158  0.013158  0.004082  0.010989  0.010989  0.000000  0.051118   
1064  0.016447  0.016447  0.004082  0.007326  0.007326  0.000000  0.030351   
1065  0.016447  0.016447  0.004082  0.007326  0.007326  0.000000  0.030351   
1066  0.000000  0.000000  0.004082  0.007326  0.007326  0.000000  0.030351   
1067  0.000000  0.000000  0.000000  0.000000  0.000000  0.003333  0.030351   

            14  
0     0.027651  
1     0.028701  
2     0.002032  
3     0.036275  
4     0.108650  
...        ...  
1063  0.000270  
1064  0.007161  
1065  0.000102  
1066  0.000210  
1067  0.000057  

[1068 rows x 15 columns]

In [126]:
# Step 4: Calculate silhouette score and sort clusters
def get_optimal_clusters(data):
    scores = []
    # for n_clusters in range(2, len(data) +1):
    #     kmeans = KMeans(n_clusters=n_clusters)
    #     sil_avg = silhouette_score(data, kmeans.labels_).round(4)
    #     scores.append((sil_avg, n_clusters)

    for n_clusters in range(2, len(data)):
        km = KMeans(n_clusters = n_clusters)
        km.fit(data)
        sil_avg = silhouette_score(data, km.labels_).round(4)
        scores.append([sil_avg , n_clusters])
    scores.sort(reverse=True)
    return scores[:5]

In [127]:
# Step 5: Perform KMeans clustering
# def perform_clustering(data_original, df_process,  num_clusters):
#     kmeans = KMeans(n_clusters=num_clusters)
#     # kmeans.fit_predict(df_process)
#     cluster_labels = kmeans.fit_predict(df_process)
#     data_original['cluster'] = cluster_labels
#     return data_original

In [128]:
data = X.iloc[:, [0,1,2]]

In [129]:
num_clusters = get_optimal_clusters(data)

c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with M

In [134]:
num_clusters

[[0.9852, 2], [0.9794, 3], [0.9575, 4], [0.8482, 5], [0.841, 6]]

In [135]:
from sklearn.cluster import KMeans

kmeans = KMeans(n_clusters=num_clusters)
kmeans

KMeans(n_clusters=[[0.9852, 2], [0.9794, 3], [0.9575, 4], [0.8482, 5],
                   [0.841, 6]])

In [132]:
# df['cluster'] = cluster_labels

In [139]:
cluster_labels = kmeans.fit_predict(data)

InvalidParameterError: The 'n_clusters' parameter of KMeans must be an int in the range [1, inf). Got [[0.9852, 2], [0.9794, 3], [0.9575, 4], [0.8482, 5], [0.841, 6]] instead.

In [ ]:
# clustered_data = perform_clustering(df, X.iloc[:,[0,1,2]], num_clusters)

In [ ]:
# Step 6, 7, and 8: Get cluster information
def get_cluster_info(cluster_data):
    cluster_info = []
    # Replace with your time column name
    time_column = 'time'

    for cluster_num in cluster_data['cluster'].unique():
        cluster_subset = cluster_data[cluster_data['cluster'] == cluster_num]
        time_min = cluster_subset[time_column].min()
        time_max = cluster_subset[time_column].max()
        time_std = cluster_subset[time_column].std()
        time_minus_2std = time_min - 2 * time_std
        time_minus_1std = time_min - time_std
        time_plus_1std = time_max + time_std
        time_plus_2std = time_max + 2 * time_std

        cluster_info.append({
            'cluster_num': cluster_num,
            'time_min': time_min,
            'time_max': time_max,
            'time_minus_2std': time_minus_2std,
            'time_minus_1std': time_minus_1std,
            'time_plus_1std': time_plus_1std,
            'time_plus_2std': time_plus_2std
        })

    return cluster_info

In [ ]:
from itertools import combinations
import pandas as pd

# Step 1: Loop through combinations
def column_combinations(data_frame):
    columns = data_frame.columns
    col_combinations = []

    for r in range(1, len(columns) + 1):
        for combo in combinations(columns, r):
            col_combinations.append(combo)

    return col_combinations

# Main function
def main():
    data = X.iloc[:, [0,1,2]]
    combinations_list = column_combinations(data)
    print('Combinations_list ::::' , combinations_list)

    results = []
    for combination in combinations_list:
        # print('DATA ::', data)
        # print('=====================')


        scaled_data = scale_data(data , data.columns)
        print('SCALED ::', scaled_data)
        print('====================')

        num_clusters = get_optimal_clusters(scaled_data)
        print('NUM ::', num_clusters)
        print('====================')

        clustered_data = perform_clustering(df,data, num_clusters)
        print("CLUSTERRED DATA ::", clustered_data)
        print('====================')

        cluster_info = get_cluster_info(clustered_data)
        print("CL cluster_info ::" , cluster_info)
        print('====================')


        for info in cluster_info:
            result_dict = {
                'combination': combination,
                'cluster_num': info['cluster_num'],
                'silhouette_score': get_optimal_clusters(scaled_data),
                'cluster_sort': num_clusters,
                'time_min': info['time_min'],
                'time_max': info['time_max'],
                'time_minus_2std': info['time_minus_2std'],
                'time_minus_1std': info['time_minus_1std'],
                'time_plus_1std': info['time_plus_1std'],
                'time_plus_2std': info['time_plus_2std']
            }
            results.append(result_dict)

    results_df = pd.DataFrame(results)
    results_df.to_csv('output_results_2.csv', index=False)  # Save results to CSV

if __name__ == "__main__":
    main()


Combinations_list :::: [('commits',), ('additions',), ('deletions',), ('commits', 'additions'), ('commits', 'deletions'), ('additions', 'deletions'), ('commits', 'additions', 'deletions')]
SCALED ::              0         1         2
0     0.000000  0.000262  0.000143
1     0.000000  0.000052  0.000036
2     0.000000  0.000944  0.002393
3     0.000000  0.000551  0.000071
4     0.060870  0.005536  0.007571
...        ...       ...       ...
1063  0.026087  0.005011  0.001428
1064  0.043478  0.012330  0.001500
1065  0.008696  0.001810  0.001750
1066  0.000000  0.000289  0.040283
1067  0.000000  0.000944  0.000000

[1068 rows x 3 columns]


c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with MKL, when there are less chunks than available threads. You can avoid it by setting the environment variable OMP_NUM_THREADS=5.
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:870: FutureWarning: The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning
  warnings.warn(
c:\Users\patcharaprapa_k\AppData\Local\anaconda3\lib\site-packages\sklearn\cluster\_kmeans.py:1382: UserWarning: KMeans is known to have a memory leak on Windows with M

NUM :: [[0.85, 2], [0.8369, 3], [0.7898, 4], [0.7234, 7], [0.7229, 6]]


C:\Users\patcharaprapa_k\AppData\Local\Temp\ipykernel_8572\3737300273.py:11: ConvergenceWarning: Number of distinct clusters (846) found smaller than n_clusters (1067). Possibly due to duplicate points in X.
  km.fit(data)


InvalidParameterError: The 'n_clusters' parameter of KMeans must be an int in the range [1, inf). Got [[0.85, 2], [0.8369, 3], [0.7898, 4], [0.7234, 7], [0.7229, 6]] instead.

In [ ]:
X.columns[:3]

Index(['commits', 'additions', 'deletions'], dtype='object')

In [ ]:
X.iloc[:, [0,1,2,14]]

commits  additions  deletions              time
0           1         10          4   264468000000000
1           1          2          1   274510000000000
2           1         36         67    19443000000000
3           1         21          2   346946000000000
4           8        211        212  1039167000000000
...       ...        ...        ...               ...
1063        4        191         40     2590000000000
1064        6        470         42    68499000000000
1065        2         69         49      982000000000
1066        1         11       1128     2015000000000
1067        1         36          0      554000000000

[1068 rows x 4 columns]

In [ ]:
rf = pd.read_csv('output_results_2.csv')
rf

In [ ]:
rf['time_min'] = pd.to_timedelta(rf['time_min'])
rf['time_max'] = pd.to_timedelta(rf['time_max'])
rf['time_minus_1std'] = pd.to_timedelta(rf['time_minus_1std'])
rf['time_minus_2std'] = pd.to_timedelta(rf['time_minus_2std'])
rf['time_plus_1std'] = pd.to_timedelta(rf['time_plus_1std'])
rf['time_plus_2std'] = pd.to_timedelta(rf['time_plus_2std'])

In [ ]:
rf

combination  cluster_num  \
0                                    ('commits',)            0   
1                                    ('commits',)            1   
2                                  ('additions',)            0   
3                                  ('additions',)            1   
4                                  ('deletions',)            0   
5                                  ('deletions',)            1   
6                                       ('time',)            0   
7                                       ('time',)            1   
8                        ('commits', 'additions')            0   
9                        ('commits', 'additions')            1   
10                       ('commits', 'deletions')            0   
11                       ('commits', 'deletions')            2   
12                       ('commits', 'deletions')            1   
13                            ('commits', 'time')            0   
14                            ('commits', 'time')            1   
15                     ('additions', 'deletions')            0   
16                     ('additions', 'deletions')            1   
17                          ('additions', 'time')            0   
18                          ('additions', 'time')            1   
19                          ('additions', 'time')            2   
20                          ('deletions', 'time')            0   
21                          ('deletions', 'time')            2   
22                          ('deletions', 'time')            1   
23          ('commits', 'additions', 'deletions')            0   
24          ('commits', 'additions', 'deletions')            1   
25               ('commits', 'additions', 'time')            0   
26               ('commits', 'additions', 'time')            2   
27               ('commits', 'additions', 'time')            1   
28               ('commits', 'deletions', 'time')            1   
29               ('commits', 'deletions', 'time')            0   
30             ('additions', 'deletions', 'time')            0   
31             ('additions', 'deletions', 'time')            2   
32             ('additions', 'deletions', 'time')            1   
33  ('commits', 'additions', 'deletions', 'time')            0   
34  ('commits', 'additions', 'deletions', 'time')            1   

    silhouette_score  cluster_sort         time_min          time_max  \
0                  2             2  0 days 00:00:05  18 days 05:11:10   
1                  2             2 19 days 10:49:37 110 days 16:44:58   
2                  2             2  0 days 00:00:05  18 days 05:11:10   
3                  2             2 19 days 10:49:37 110 days 16:44:58   
4                  2             2  0 days 00:00:05  18 days 05:11:10   
5                  2             2 19 days 10:49:37 110 days 16:44:58   
6                  2             2  0 days 00:00:05  18 days 05:11:10   
7                  2             2 19 days 10:49:37 110 days 16:44:58   
8                  2             2  0 days 00:00:05  18 days 05:11:10   
9                  2             2 19 days 10:49:37 110 days 16:44:58   
10                 3             3  0 days 00:00:05   7 days 09:20:19   
11                 3             3  7 days 12:04:52  29 days 12:33:22   
12                 3             3 30 days 19:11:30 110 days 16:44:58   
13                 3             2  0 days 00:00:05  18 days 05:11:10   
14                 3             2 19 days 10:49:37 110 days 16:44:58   
15                 2             2  0 days 00:00:05  18 days 05:11:10   
16                 2             2 19 days 10:49:37 110 days 16:44:58   
17                 3             3  0 days 00:00:05   7 days 09:20:19   
18                 3             3  7 days 12:04:52  29 days 12:33:22   
19                 3             3 30 days 19:11:30 110 days 16:44:58   
20                 3             3  0 days 00:00:05   7 days 05:05:12   
21                 3             3  7 days 06:51:27  29